## Model

In [1]:
using ReachabilityAnalysis, Plots

In [2]:
# the default options give a natural frequency ωₙ = 6.28rad/s and 
# natural period Tₙ=1
function spring_mass(; k = 39.47, # N/m 
                       m = 1.0, # kg
                       c = 0.0, # no damping
                       U = Interval(0, 0),  # no forcing term
                       μx0 = 1e-5, # initial spread in position
                       μv0 = 1e-5, # initial spread in velocity
                       X0 = Ellipsoid([μx0 0; 0. μv0]), # shape of the initial states
                       X = Universe(2)) # no state constraints 
    A = [0 1; -k/m -c/m]
    b = [0, 1/m]
    prob = @ivp(x' = A*x + b*u, x(0) ∈ X0, u ∈ U, x ∈ X)
    return prob
end

spring_mass (generic function with 1 method)

## Solution without damping

In [3]:
# between 0 and 3 sec the forcing term is zero
prob = spring_mass();
@time sol1 = solve(prob, tspan=(0.0, 3.0), alg=BOX(δ=1e-2));

# between 3 and 3.4sec the forcing term is one
prob = spring_mass(U=Interval(1, 1), X0=set(sol1[end]));
@time sol2 = solve(prob, tspan=(0.0, 0.4), alg=BOX(δ=1e-2), Δt0=3.0 .. 3.0);

# between 3.4 and 10sec the forcing term is zero
prob = spring_mass(U=Interval(0, 0), X0=set(sol2[end]));
@time sol3 = solve(prob, tspan=(0.0, 10-3.4), alg=BOX(δ=1e-2), Δt0=3.4 .. 3.4);

# assemble solution
sol = HybridFlowpipe([sol1.F, sol2.F, sol3.F]);

  4.712964 seconds (10.07 M allocations: 492.359 MiB, 4.04% gc time)
  0.295149 seconds (439.88 k allocations: 23.591 MiB)
  0.000690 seconds (4.79 k allocations: 495.859 KiB)


In [4]:
plotly()

┌ Info: For saving to png with the Plotly backend ORCA has to be installed.
└ @ Plots /home/mforets/.julia/packages/Plots/sbXPh/src/backends.jl:373


Plots.PlotlyBackend()

In [5]:
plot(sol[1], vars=(0, 1), lw=0.1, xlab="time [s]", ylab="displacement [m]")
plot!(sol[2], vars=(0, 1), lw=0.1, xlab="time [s]", ylab="displacement [m]")
plot!(sol[3], vars=(0, 1), lw=0.1, xlab="time [s]", ylab="displacement [m]")

<!DOCTYPE html>
 
 
 Plots.jl

In [6]:
plot(sol[1], vars=(0, 1), lw=0.1, xlab="time [s]", ylab="velocity [m/s]")
plot!(sol[2], vars=(0, 1), lw=0.1, xlab="time [s]", ylab="velocity [m/s]")
plot!(sol[3], vars=(0, 1), lw=0.1, xlab="time [s]", ylab="velocity [m/s]")

<!DOCTYPE html>
 
 
 Plots.jl

### TODO: hacer graficas en 3D 

In [7]:
plot(sol1, vars=(1, 2), lw=0.1)

<!DOCTYPE html>
 
 
 Plots.jl

## Solution with damping

In [8]:
# between 0 and 3 sec the forcing term is zero
prob = spring_mass(c=0.1);
@time sol1 = solve(prob, tspan=(0.0, 3.0), alg=BOX(δ=1e-2));

# between 3 and 3.4sec the forcing term is one
prob = spring_mass(c=0.1, U=Interval(1, 1), X0=set(sol1[end]));
@time sol2 = solve(prob, tspan=(0.0, 0.4), alg=BOX(δ=1e-2), Δt0=3.0 .. 3.0);

# between 3.4 and 10sec the forcing term is zero
prob = spring_mass(c=0.1, U=Interval(0, 0), X0=set(sol2[end]));
@time sol3 = solve(prob, tspan=(0.0, 10-3.4), alg=BOX(δ=1e-2), Δt0=3.4 .. 3.4);

# assemble solution
sol = HybridFlowpipe([sol1.F, sol2.F, sol3.F]);

  0.000962 seconds (2.28 k allocations: 237.828 KiB)
  0.000168 seconds (452 allocations: 50.078 KiB)
  0.001534 seconds (4.79 k allocations: 495.859 KiB)


In [9]:
plot(sol[1], vars=(0, 1), lw=0.1, xlab="time [s]", ylab="displacement [m]")
plot!(sol[2], vars=(0, 1), lw=0.1, xlab="time [s]", ylab="displacement [m]")
plot!(sol[3], vars=(0, 1), lw=0.1, xlab="time [s]", ylab="displacement [m]")

<!DOCTYPE html>
 
 
 Plots.jl

## References

[1] Scacchioli, A., Bayen, A. M., & Stojadinović, B. (2014). Assessment of uncertainty propagation in the dynamic response of single-degree-of-freedom structures using reachability analysis. Journal of Engineering Mechanics, 140(6), 04014038. pdf



